In [1]:
###imports
import os
import pandas
import re
import sqlite3
import pandas as pd
import csv
import chardet
import json

In [2]:
###文件路径
db_path = "E:/SAIRI/TAVI/Code/data/TAVI_data.db"#数据库路径
csv_file = "E:/SAIRI/TAVI/Code/data/output_with_pubmed_data.csv"#csv_路径
pdf_dir = "E:/SAIRI/TAVI/Code/pdf_downloads"#pdf的文件夹路径
layout_root = "E:/SAIRI/TAVI/Code/extract_downloads"#其他文件夹路径
json_folder = "E:/SAIRI/TAVI/Code/extract_features"#featurejson的路径
output_json_path = "E:/SAIRI/TAVI/Code/data/db_output.json"#输出路径

In [3]:
###核对现在的数据库路径
db_path1 = os.path.abspath(db_path)  
print("数据库文件路径:", db_path1)

数据库文件路径: E:\SAIRI\TAVI\Code\data\TAVI_data.db


In [ ]:
###建表语句，在数据库管理软件直接跑，或者用python连接后pao
##目前按照来源建表，可根据实际要求更改
##对于混合数据（如数字+符号）采用TEXT类型，之后若实际情况需要aggregate类操作可以考虑更改
##二元内容目前采用0/1
##部分可以用int节省存储的情况采用varchar，防止前导0的情况导致0012变成12之类的

#来自feature extraction json
#1
CREATE TABLE feature_extraction_result (
    doi VARCHAR(255) UNIQUE,
    death TINYINT(1),
    paravalvular_leak TINYINT(1),
    mean_aortic_gradient VARCHAR(255),
    peak_aortic_gradients VARCHAR(255),
    valve_area VARCHAR(255),
    maximum_velocity VARCHAR(255)     

)

#1
CREATE TABLE feature_extraction_procedure(
    doi VARCHAR(255) UNIQUE,
    valve_diameter VARCHAR(255),
    valve_type VARCHAR(255)

)

#1
CREATE TABLE feature_extraction_pre_info(
    doi VARCHAR(255) UNIQUE,
    mean_gradient VARCHAR(255),
    peak_gradients VARCHAR(255),
    valve_area VARCHAR(255),
    maximum_velocity VARCHAR(255),
    ejection_fraction VARCHAR(255)
)

#1
CREATE TABLE feature_extraction_basic_info(
    doi VARCHAR(255) UNIQUE,
    age INT,
    gender TINYINT(1),
    case1 VARCHAR(255),
    previous_history VARCHAR(255)
)

#来自跑出来的csv
#1
CREATE TABLE from_csv(
    doi VARCHAR(255) UNIQUE, 
    article_title VARCHAR(255),
    source_title VARCHAR(255),
    pmid VARCHAR(10),
    year INT,
    abstract TEXT,
    authors VARCHAR(255),
    keywords VARCHAR(255) 

)

#来自layout以及图片信息
#1
CREATE TABLE from_layout(
    doi VARCHAR(255),
    pdf_path VARCHAR(255),
    image_path VARCHAR(255),
    image_caption TEXT
)

##所有的TEXT或许都用VARCHAR(255)也够用

SyntaxError: invalid syntax (883060680.py, line 5)

In [10]:
#已跑通
###python制表示例
conn = sqlite3.connect(db_path)
cursor = conn.cursor()
cursor.execute('''
CREATE TABLE from_layout(
    doi VARCHAR(255),
    pdf_path VARCHAR(255),
    image_path VARCHAR(255),
    image_caption TEXT
)
    ''')
conn.commit()
conn.close()
print("数据库表已创建。")

数据库表已创建。


In [24]:
# #已跑通
# ###python清表示例
# conn = sqlite3.connect(db_path)
# cursor = conn.cursor()
# table_name = "feature_extraction_result"#要删除的表名

# #删除整个表
# #cursor.execute(f"DROP TABLE IF EXISTS {table_name};")
# #print(f"表 {table_name} 已彻底删除")

# #仅清空数据
# cursor.execute(f"DELETE FROM {table_name};")
# print(f"表 {table_name} 数据已清空")
        
# conn.commit()
# conn.close()



表 feature_extraction_result 数据已清空


In [11]:
#已跑通
###从csv里读取数据并插入表
def insert_from_csv(csv_file, db_path):
    # 自动检测 CSV 文件编码
    with open(csv_file, "rb") as f:
        result = chardet.detect(f.read())  # 获取文件编码
        file_encoding = result['encoding']

    conn = sqlite3.connect(db_path)
    cursor = conn.cursor()
    print("开始从csv写入表")
    with open(csv_file, "r", encoding=file_encoding) as f:
        reader = csv.DictReader(f, delimiter=",")  # 你的 CSV 用的是 Tab 分隔符

        for row in reader:
            # 处理 Year，确保是整数
            year = row["Year"].strip()
            year = int(year) if year.isdigit() else None  # 如果无法转换，则设为 None
            
            # 处理 Keywords，转换 "N/A" 为 NULL
            keywords = row["Keywords"].strip()
            keywords = None if keywords.upper() == "N/A" else keywords
            
            # 执行插入
            cursor.execute('''
                INSERT OR IGNORE INTO from_csv(doi, article_title, source_title, pmid, year, abstract, authors, keywords)
                VALUES (?, ?, ?, ?, ?, ?, ?, ?)
            ''', (
                row["DOI"],  
                row["Article Title"],
                row["Source Title"],
                row["Pubmed Id"],
                year,
                row["Abstract"],
                row["Authors"],
                keywords
            ))

    conn.commit()
    conn.close()
    print("csv数据插入完成。")


In [12]:
#已跑通
###从特征json写入表
def extract_age(value):
    value = value.strip()
    if value.upper() == "N/A":
        return -1
    numbers = re.findall(r'\d+', value)
    return int(numbers[0]) if numbers else -1

def insert_json_to_db(json_folder, db_path):
    
    conn = sqlite3.connect(db_path)
    cursor = conn.cursor()
    print("开始写入特征 JSON 数据")
    # 遍历指定文件夹下所有 JSON 文件
    for file_name in os.listdir(json_folder):
        if file_name.lower().endswith(".json"):
            file_path = os.path.join(json_folder, file_name)
            print(f"处理文件: {file_path}")
            with open(file_path, "r", encoding="utf-8") as f:
                data = json.load(f)
            
            # 如果文件内容是数组格式，则遍历每个记录，否则直接处理单个记录
            records = data if isinstance(data, list) else [data]
            
            for record in records:
                doi = record.get("doi", "").strip()
                if not doi:
                    continue  # 如果 DOI 为空，则跳过该记录
                # 处理 DOI，将下划线转换成斜杠
                doi = doi.replace("_", "/")
                
                # Basic_Info 
                basic_info = record.get("result", {}).get("Basic_Info", {})
                age = extract_age(basic_info.get("Age", "N/A"))
                gender_str = basic_info.get("Gender", "").strip().lower()
                gender = 1 if gender_str == "male" else 0  # Male=1, Female=0
                case1 = basic_info.get("Case", "")
                previous_history = basic_info.get("Previous_History", "")
                cursor.execute('''
                    INSERT OR IGNORE INTO feature_extraction_basic_info (doi, age, gender, case1, previous_history)
                    VALUES (?, ?, ?, ?, ?)
                ''', (doi, age, gender, case1, previous_history))

                # Pre_Info
                pre_info = record.get("result", {}).get("Pre_Info", {})
                mean_gradient = pre_info.get("Mean_Aortic_Gradient", "N/A")
                peak_gradients = pre_info.get("Peak_Aortic_Gradients", "N/A")
                valve_area_pre = pre_info.get("Valve_Area", "N/A")
                maximum_velocity_pre = pre_info.get("Maximum_Velocity", "N/A")
                ejection_fraction = pre_info.get("Ejection_Fraction", "N/A")
                cursor.execute('''
                    INSERT OR IGNORE INTO feature_extraction_pre_info (doi, mean_gradient, peak_gradients, valve_area, maximum_velocity, ejection_fraction)
                    VALUES (?, ?, ?, ?, ?, ?)
                ''', (doi, mean_gradient, peak_gradients, valve_area_pre, maximum_velocity_pre, ejection_fraction))

                # Procedure
                procedure = record.get("result", {}).get("Procedure", {})
                valve_diameter = procedure.get("Valve_Diameter", "N/A")
                valve_type = procedure.get("Valve_Type", "N/A")
                cursor.execute('''
                    INSERT OR IGNORE INTO feature_extraction_procedure (doi, valve_diameter, valve_type)
                    VALUES (?, ?, ?)
                ''', (doi, valve_diameter, valve_type))
                
                # Result
                result_section = record.get("result", {}).get("Result", {})
                death = 1 if result_section.get("Death") else 0
                paravalvular_leak = 1 if result_section.get("Paravalvular_Leak") else 0
                mean_aortic_gradient = result_section.get("Mean_Aortic_Gradient", "N/A")
                peak_aortic_gradients = result_section.get("Peak_Aortic_Gradients", "N/A")
                valve_area_result = result_section.get("Valve_Area", "N/A")
                maximum_velocity_result = result_section.get("Maximum_Velocity", "N/A")
                cursor.execute('''
                    INSERT OR IGNORE INTO feature_extraction_result (doi, death, paravalvular_leak, mean_aortic_gradient, peak_aortic_gradients, valve_area, maximum_velocity)
                    VALUES (?, ?, ?, ?, ?, ?, ?)
                ''', (doi, death, paravalvular_leak, mean_aortic_gradient, peak_aortic_gradients, valve_area_result, maximum_velocity_result))
    
    conn.commit()
    conn.close()
    print("所有特征JSON记录数据已写入数据库。")


In [13]:
#已跑通
###layout写入表

def clean_caption(caption):
    
    cleaned_caption = re.sub(r'^(?:fig(?:ure)?\.?\s*\d*[\.\s-]*)', '', caption, flags=re.IGNORECASE) #可根据要求更改
    return cleaned_caption.strip()

def insert_layout_data(pdf_folder, layout_root, db_path):
    conn = sqlite3.connect(db_path)
    cursor = conn.cursor()

    print("\n=== 开始处理 PDF 文件 ===")
    pdf_files = os.listdir(pdf_folder)
    print(f"在 {pdf_folder} 目录下找到 {len(pdf_files)} 个文件：", pdf_files)

    for pdf_file in pdf_files:
        if not pdf_file.lower().endswith(".pdf"):
            print(f"跳过非 PDF 文件：{pdf_file}")
            continue
        
        pdf_full_path = os.path.join(pdf_folder, pdf_file)
        pdf_name_raw = os.path.splitext(pdf_file)[0]  # 去掉扩展名
        doi_converted = pdf_name_raw.replace("_", "/")  # 生成 DOI

        print(f"\n>>> 处理 PDF 文件: {pdf_file}")
        print(f"    生成 DOI: {doi_converted}")
        print(f"    PDF 完整路径: {pdf_full_path}")

        # 找到 layout 文件夹
        layout_dir = os.path.join(layout_root, pdf_name_raw)
        if not os.path.isdir(layout_dir):
            print(f"未找到 layout 文件夹：{layout_dir}，跳过 {pdf_file}")
            continue

        # images 目录
        images_dir = os.path.join(layout_dir, "images")
        if not os.path.isdir(images_dir):
            print(f"未找到 images 文件夹：{images_dir}，后续 image_path 设为 N/A")
            image_files_dict = {}
        else:
            image_files = [f for f in os.listdir(images_dir) if os.path.isfile(os.path.join(images_dir, f))]
            image_files_dict = {f: os.path.join(images_dir, f) for f in image_files}
            print(f"    在 {images_dir} 中找到 {len(image_files)} 张图片：", image_files)
        
        # 找到 _content_list.json 文件
        content_list_file = None
        for filename in os.listdir(layout_dir):
            if filename.endswith("_content_list.json"):
                content_list_file = os.path.join(layout_dir, filename)
                break

        if not content_list_file:
            print(f"未找到 _content_list.json 文件，跳过 {pdf_file}")
            continue

        print(f"    读取 content_list.json 文件：{content_list_file}")
        with open(content_list_file, "r", encoding="utf-8") as f:
            try:
                content_list_data = json.load(f)
            except Exception as e:
                print(f"    解析 {content_list_file} 出错: {e}，跳过 {pdf_file}")
                continue

        # 遍历 content_list_data，提取 image_path 和 img_caption
        extracted_images = []
        for entry in content_list_data:
            if entry.get("type") == "image":
                img_path = entry.get("img_path", "").strip()
                if img_path.startswith("images/"):
                    img_filename = img_path.replace("images/", "")
                else:
                    img_filename = img_path

                full_image_path = image_files_dict.get(img_filename, "N/A")
                img_caption_list = entry.get("img_caption", [])
                # 合并 caption，并调用 clean_caption 去掉前缀
                img_caption = " ".join(img_caption_list) if img_caption_list else "N/A"
                img_caption = clean_caption(img_caption)
                
                extracted_images.append((full_image_path, img_caption))
                print(f"        发现图片: {img_filename}")
                print(f"        图片路径: {full_image_path}")
                print(f"        原始图片说明: {' '.join(img_caption_list) if img_caption_list else 'N/A'}")
                print(f"        清理后图片说明: {img_caption}")

        # 遍历 extracted_images，将数据写入数据库
        for full_image_path, img_caption in extracted_images:
            cursor.execute('''
                INSERT OR IGNORE INTO from_layout (doi, pdf_path, image_path, image_caption)
                VALUES (?, ?, ?, ?)
            ''', (doi_converted, pdf_full_path, full_image_path, img_caption))

    conn.commit()
    conn.close()
    print("所有 layout 数据已写入数据库")


In [14]:
###sql合并写成json
def merge_data(db_path, output_json_path):
    conn = sqlite3.connect(db_path)
    conn.row_factory = sqlite3.Row  # 使查询结果以字典形式返回
    cursor = conn.cursor()

    # 以 from_csv 表为主
    cursor.execute("SELECT * FROM from_csv")
    csv_records = cursor.fetchall()

    merged_list = []
    auto_id = 1

    for rec in csv_records:
        rec = dict(rec)  # 转换为普通字典，可以使用 get 方法
        doi = rec["doi"]
        # 尝试从 from_layout 中获取 PDF 路径（假设所有记录中 PDF 路径相同）
        cursor.execute("SELECT pdf_path FROM from_layout WHERE doi = ?", (doi,))
        layout_pdf_rows = cursor.fetchall()
        if layout_pdf_rows:
            pdf_path = layout_pdf_rows[0]["pdf_path"]
        else:
            pdf_path = rec.get("pdf_path", "N/A")

        # 基本信息
        cursor.execute("SELECT * FROM feature_extraction_basic_info WHERE doi = ?", (doi,))
        basic = cursor.fetchone()
        if basic:
            basic = dict(basic)
            basic_info = {
                "Age": basic["age"],
                "Gender": "Male" if basic["gender"] == 1 else "Female",
                "Case": basic["case1"],
                "Previous_History": basic["previous_history"]
            }
        else:
            basic_info = {}

        # 预处理信息
        cursor.execute("SELECT * FROM feature_extraction_pre_info WHERE doi = ?", (doi,))
        pre = cursor.fetchone()
        if pre:
            pre = dict(pre)
            pre_info = {
                "Mean_Gradient": pre["mean_gradient"],
                "Peak_Gradients": pre["peak_gradients"],
                "Valve_Area": pre["valve_area"],
                "Maximum_Velocity": pre["maximum_velocity"],
                "Ejection_Fraction": pre["ejection_fraction"]
            }
        else:
            pre_info = {}

        # 过程信息
        cursor.execute("SELECT * FROM feature_extraction_procedure WHERE doi = ?", (doi,))
        proc = cursor.fetchone()
        if proc:
            proc = dict(proc)
            procedure = {
                "Valve_Diameter": proc["valve_diameter"],
                "Valve_Type": proc["valve_type"]
            }
        else:
            procedure = {}

        # 结果信息
        cursor.execute("SELECT * FROM feature_extraction_result WHERE doi = ?", (doi,))
        res_rec = cursor.fetchone()
        if res_rec:
            res_rec = dict(res_rec)
            result_info = {
                "Death": True if res_rec["death"] == 1 else False,
                "Paravalvular_Leak": True if res_rec["paravalvular_leak"] == 1 else False,
                "Mean_Gradient": res_rec["mean_aortic_gradient"],
                "Peak_Gradients": res_rec["peak_aortic_gradients"],
                "Valve_Area": res_rec["valve_area"],
                "Maximum_Velocity": res_rec["maximum_velocity"]
            }
        else:
            result_info = {}

        # 文件信息：PDF 路径来自 from_layout（如果有），Images 来自 from_layout（可能多条）
        cursor.execute("SELECT * FROM from_layout WHERE doi = ?", (doi,))
        layout_rows = cursor.fetchall()
        images = []
        for row in layout_rows:
            row = dict(row)
            images.append({
                "path": row["image_path"],
                "caption": row["image_caption"]
            })
        files_info = {
            "PDF": pdf_path,
            "Images": images
        }

        merged_record = {
            "id": auto_id,
            "doi": doi,
            "pmid": rec.get("pmid", ""),
            "title": rec.get("article_title", ""),
            "source": rec.get("source_title", ""),
            "Author": rec.get("authors", ""),
            "Abstract": rec.get("abstract", ""),
            "Keywords": rec.get("keywords", ""),
            "year": rec.get("year", ""),
            "Basic_Info": basic_info,
            "Pre_Info": pre_info,
            "Procedure": procedure,
            "Result": result_info,
            "Files": files_info
        }
        merged_list.append(merged_record)
        auto_id += 1

    conn.close()

    with open(output_json_path, "w", encoding="utf-8") as f_out:
        json.dump(merged_list, f_out, indent=4, ensure_ascii=False)

    print(f"Merged JSON data written to {output_json_path}")


In [15]:
###main函数

if __name__ == "__main__":
    insert_from_csv(csv_file,db_path)
    insert_json_to_db(json_folder,db_path)
    insert_layout_data(pdf_dir, layout_root, db_path)    
    merge_data(db_path, output_json_path)
    print('Done')



开始从csv写入表
csv数据插入完成。
开始写入特征 JSON 数据
处理文件: E:/SAIRI/TAVI/Code/extract_features\feature_extraction_0.json
处理文件: E:/SAIRI/TAVI/Code/extract_features\feature_extraction_100.json
处理文件: E:/SAIRI/TAVI/Code/extract_features\feature_extraction_1000.json
处理文件: E:/SAIRI/TAVI/Code/extract_features\feature_extraction_1100.json
处理文件: E:/SAIRI/TAVI/Code/extract_features\feature_extraction_1200.json
处理文件: E:/SAIRI/TAVI/Code/extract_features\feature_extraction_200.json
处理文件: E:/SAIRI/TAVI/Code/extract_features\feature_extraction_300.json
处理文件: E:/SAIRI/TAVI/Code/extract_features\feature_extraction_400.json
处理文件: E:/SAIRI/TAVI/Code/extract_features\feature_extraction_500.json
处理文件: E:/SAIRI/TAVI/Code/extract_features\feature_extraction_600.json
处理文件: E:/SAIRI/TAVI/Code/extract_features\feature_extraction_700.json
处理文件: E:/SAIRI/TAVI/Code/extract_features\feature_extraction_800.json
处理文件: E:/SAIRI/TAVI/Code/extract_features\feature_extraction_900.json
所有特征JSON记录数据已写入数据库。

=== 开始处理 PDF 文件 ===
在 E:/SAIRI/T